In [1]:
import tensorflow as tf
print('Tensorflow version:',tf.__version__)
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
%matplotlib inline
plt.style.use('seaborn')
import seaborn as sns
from sklearn.model_selection import train_test_split 
import os
print('Keras version:', tf.keras.__version__)

import tensorflow_datasets as tfds
from tensorflow.keras import Sequential
from tensorflow.keras.layers import *
from tensorflow.keras.optimizers import *
from tensorflow.keras.callbacks import ModelCheckpoint, TensorBoard, EarlyStopping

from mpl_toolkits.mplot3d import Axes3D
from sklearn.preprocessing import StandardScaler
from glob import glob
from PIL import Image

Tensorflow version: 2.0.0
Keras version: 2.2.4-tf


In [2]:
print(os.listdir("/Users/natalieko/Desktop/RespiratoryDiagnosis"))

['.DS_Store', 'Test', 'Train']


In [3]:
folder_COPD_train = '/Users/natalieko/Desktop/RespiratoryDiagnosis/Train/COPD'
folder_Healthy_train = '/Users/natalieko/Desktop/RespiratoryDiagnosis/Train/Healthy'
folder_Pneumonia_train = '/Users/natalieko/Desktop/RespiratoryDiagnosis/Train/Pneumonia'
folder_Asthma_train = '/Users/natalieko/Desktop/RespiratoryDiagnosis/Train/Asthma'

folder_COPD_test = '/Users/natalieko/Desktop/RespiratoryDiagnosis/Test/COPD'
folder_Healthy_test = '/Users/natalieko/Desktop/RespiratoryDiagnosis/Test/Healthy'
folder_Pneumonia_test = '/Users/natalieko/Desktop/RespiratoryDiagnosis/Test/Pneumonia'
folder_Asthma_test = '/Users/natalieko/Desktop/RespiratoryDiagnosis/Test/Asthma'

read = lambda imname: np.asarray(Image.open(imname).convert("RGB").resize((401, 262)))

In [4]:
# Load in training pictures 
ims_COPD = [read(os.path.join(folder_COPD_train, filename)) for filename in os.listdir(folder_COPD_train)]
X_COPD = np.array(ims_COPD, dtype='uint64')
ims_Healthy = [read(os.path.join(folder_Healthy_train, filename)) for filename in os.listdir(folder_Healthy_train)]
X_Healthy = np.array(ims_Healthy, dtype='uint64')
ims_Pneumonia = [read(os.path.join(folder_Pneumonia_train, filename)) for filename in os.listdir(folder_Pneumonia_train)]
X_Pneumonia = np.array(ims_Pneumonia, dtype='uint64')
ims_Asthma = [read(os.path.join(folder_Asthma_train, filename)) for filename in os.listdir(folder_Asthma_train)]
X_Asthma = np.array(ims_Asthma, dtype='uint64')

# Load in testing pictures
ims_COPD = [read(os.path.join(folder_COPD_test, filename)) for filename in os.listdir(folder_COPD_test)]
X_COPD_test = np.array(ims_COPD, dtype='uint64')
ims_Healthy = [read(os.path.join(folder_Healthy_test, filename)) for filename in os.listdir(folder_Healthy_test)]
X_Healthy_test = np.array(ims_Healthy, dtype='uint64')
ims_Pneumonia = [read(os.path.join(folder_Pneumonia_test, filename)) for filename in os.listdir(folder_Pneumonia_test)]
X_Pneumonia_test = np.array(ims_Pneumonia, dtype='uint64')
ims_Asthma = [read(os.path.join(folder_Asthma_test, filename)) for filename in os.listdir(folder_Asthma_test)]
X_Asthma_test = np.array(ims_Asthma, dtype='uint64')

# Create labels
y_COPD = np.full(X_COPD.shape[0], 0)
y_Healthy = np.full(X_Healthy.shape[0], 1)
y_Pneumonia = np.full(X_Pneumonia.shape[0], 2)
y_Asthma = np.full(X_Asthma.shape[0], 3)

y_COPD_test = np.full(X_COPD_test.shape[0], 0)
y_Healthy_test = np.full(X_Healthy_test.shape[0], 1)
y_Pneumonia_test = np.full(X_Pneumonia_test.shape[0], 2)
y_Asthma_test = np.full(X_Asthma_test.shape[0], 3)

# Merge data 
X_train = np.concatenate((X_COPD, X_Healthy, X_Pneumonia, X_Asthma), axis = 0)
y_train = np.concatenate((y_COPD, y_Healthy,y_Pneumonia, y_Asthma), axis = 0)

X_test = np.concatenate((X_COPD_test, X_Healthy_test, X_Pneumonia_test, X_Asthma_test), axis = 0)
y_test = np.concatenate((y_COPD_test, y_Healthy_test, y_Pneumonia_test, y_Asthma_test), axis = 0)

# Shuffle data
s = np.arange(X_train.shape[0])
np.random.shuffle(s)
X_train = X_train[s]
y_train = y_train[s]

s = np.arange(X_test.shape[0])
np.random.shuffle(s)
X_test = X_test[s]
y_test = y_test[s]

In [5]:
print(f'Shape of an image: {X_train[0].shape}')
print(f'Max pixel value: {X_train.max()}')
print(f'Min pixel value: {X_train.min()}')
print(f'Classes: {np.unique(y_train)}')

Shape of an image: (262, 401, 3)
Max pixel value: 255
Min pixel value: 0
Classes: [0 1 2 3]


In [6]:
# Display first 9 images of spectrograms, and how they are classified
fig=plt.figure(figsize=(401, 262))
columns = 3
rows = 3

for i in range(1, columns*rows +1):
    ax = fig.add_subplot(rows, columns, i)
    if y_train[i] == 0:
        ax.set_title('COPD', fontsize=300)
    elif y_train[i] == 1:
        ax.set_title('Healthy', fontsize=300)
    elif y_train[i] == 2:
        ax.set_title('Pneumonia', fontsize=300)
    elif y_train[i] == 3:
        ax.set_title('Asthma', fontsize=300)
    plt.imshow(X_train[i], interpolation='nearest')
plt.show()

In [7]:
X_train = X_train/255
X_test = X_test/255

num_classes = 4

train_one_hot = tf.keras.utils.to_categorical(y_train,num_classes)
test_one_hot = tf.keras.utils.to_categorical(y_test,num_classes)

print(y_train[0])
print(train_one_hot[0])

train_size = X_train.shape[0]
test_size = X_test.shape[0]


print(f'Max pixel value: {X_train.max()}')
print(f'Min pixel value: {X_train.min()}')
print(f'Train size: {train_size}, Test size: {test_size}')
print(f'Train data shape: {X_train.shape}, Test data shape: {X_test.shape}')
print(f'Train label shape: {train_one_hot.shape}, Test label shape: {test_one_hot.shape}')

3
[0. 0. 0. 1.]
Max pixel value: 1.0
Min pixel value: 0.0
Train size: 301, Test size: 74
Train data shape: (301, 262, 401, 3), Test data shape: (74, 262, 401, 3)
Train label shape: (301, 4), Test label shape: (74, 4)


In [8]:
batch_size = 301
epoch = 2000


es = EarlyStopping(
    monitor='val_accuracy',
    min_delta=0,
    patience=40,
    verbose=1,
    mode='auto',
    restore_best_weights=True
)

optimizer = tf.keras.optimizers.Adam(
    learning_rate=1e-3, beta_1=0.9, beta_2=0.999, epsilon=1e-07, amsgrad=False,
    name='Adam'
)

In [9]:
REGULARIZED_INPUT_SHAPE = [262,401,3]

X_train = X_train.reshape([-1]+REGULARIZED_INPUT_SHAPE)
X_test = X_test.reshape([-1]+REGULARIZED_INPUT_SHAPE)

print(f'Train data shape: {X_train.shape}, Test data shape: {X_test.shape}')

Train data shape: (301, 262, 401, 3), Test data shape: (74, 262, 401, 3)


In [10]:
from tensorflow.keras import regularizers

tf.keras.backend.clear_session()

inputs = Input(shape=REGULARIZED_INPUT_SHAPE)

X = Conv2D(filters=64, kernel_size=(4,4), strides=(1,1), 
           activation='relu', padding='same')(inputs)

X = MaxPool2D(pool_size=(2, 2), strides=(2,2))(X)

X = Dropout(0.2)(X)

X = Conv2D(filters=64, kernel_size=(4,4), strides=(1,1) , activation='relu')(X)
                    
X = MaxPool2D(pool_size=(2, 2), strides=(2,2))(X)

X = Dropout(0.2)(X)

X = Conv2D(filters=64, kernel_size=(4,4), strides=(1,1) , activation='relu')(X)
                    
X = MaxPool2D(pool_size=(2, 2), strides=(2,2))(X)


X = Flatten()(X)

X = Dropout(0.2)(X)

X = Dense(1000, activation='relu',kernel_regularizer = regularizers.l2(0.1))(X)

X = Dropout(0.2)(X)

X = Dense(64, activation='relu',kernel_regularizer = regularizers.l2(0.1))(X)

outputs = Dense(num_classes, activation='softmax')(X)

regularized_model = tf.keras.Model(inputs=inputs,outputs=outputs, name="regularized_model")


regularized_model.summary()

2022-01-12 11:36:45.385056: I tensorflow/core/platform/cpu_feature_guard.cc:145] This TensorFlow binary is optimized with Intel(R) MKL-DNN to use the following CPU instructions in performance critical operations:  SSE4.1 SSE4.2 AVX AVX2 AVX512F FMA
To enable them in non-MKL-DNN operations, rebuild TensorFlow with the appropriate compiler flags.
2022-01-12 11:36:45.385376: I tensorflow/core/common_runtime/process_util.cc:115] Creating new thread pool with default inter op setting: 8. Tune using inter_op_parallelism_threads for best performance.


Model: "regularized_model"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         [(None, 262, 401, 3)]     0         
_________________________________________________________________
conv2d (Conv2D)              (None, 262, 401, 64)      3136      
_________________________________________________________________
max_pooling2d (MaxPooling2D) (None, 131, 200, 64)      0         
_________________________________________________________________
dropout (Dropout)            (None, 131, 200, 64)      0         
_________________________________________________________________
conv2d_1 (Conv2D)            (None, 128, 197, 64)      65600     
_________________________________________________________________
max_pooling2d_1 (MaxPooling2 (None, 64, 98, 64)        0         
_________________________________________________________________
dropout_1 (Dropout)          (None, 64, 98, 64)  

In [11]:
regularized_model.compile(loss='categorical_crossentropy',
              optimizer=optimizer,
              metrics=['accuracy'])

In [12]:
scores = regularized_model.evaluate(X_test.reshape([-1]+REGULARIZED_INPUT_SHAPE), test_one_hot, verbose=1)
names = regularized_model.metrics_names

for i in range(len(scores)):
  print(f'Regularized model test {names[i]}: {scores[i]:.4f}')

74/1 [==================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================

In [13]:
prediction = regularized_model.predict(X_test)

figure = plt.figure(figsize=(401,262))

for i, index in enumerate(np.random.choice(X_test.shape[0], size=15, replace=False)):
    ax = figure.add_subplot(3, 5, i + 1, xticks=[], yticks=[])
   
    ax.imshow(X_test[index].reshape(401,262,3), cmap='gray')
    predict_index = np.argmax(prediction[index])
    true_index = np.argmax(test_one_hot[index])

    if y_test[predict_index] == 0:
        predict_label = 'COPD'
    elif y_test[predict_index] == 1:
        predict_label = 'Healthy'
    elif y_test[predict_index] == 2:
        predict_label = 'Pneumonia'
    elif y_test[predict_index] == 3:
        predict_label = 'Asthma'
        
    if y_test[true_index] == 0:
        true_label = 'COPD'
    elif y_test[true_index] == 1:
        true_label = 'Healthy'
    elif y_test[true_index] == 2:
        true_label = 'Pneumonia'
    elif y_test[true_index] == 3:
        true_label = 'Asthma'
        
    if y_test[predict_index] == y_test[true_index]:
        label_color = "green"
    else:
        label_color = "red"
        
    ax.set_title("{} ({})".format(predict_label, true_label), color = label_color, fontsize=200)

In [17]:
model = tf.keras.Model(inputs, outputs)

In [18]:
model.save(f"{scores[1]:.4f}")

2022-01-12 12:25:10.019448: W tensorflow/python/util/util.cc:299] Sets are not currently considered sequences, but this may change in the future, so consider avoiding using them.


Instructions for updating:
If using Keras pass *_constraint arguments to layers.
INFO:tensorflow:Assets written to: 0.3514/assets
